In [1]:
import csv
import time 
import datetime
from statistics import mean, stdev
from dateutil import parser
import numpy as np

In [2]:
#Analysing 2018 january
transactions = []
with open("eos.csv") as csv_file:
    csv_reader = csv.reader(csv_file, delimiter=',')
    line_count = 0

    for row in csv_reader:

        if line_count == 0:
            headers = row
        else:
            transactions.append(row)

        line_count +=1

In [3]:
def extract_users(tx):
    return tx[3], tx[4]

def extract_types(tx):
    return tx[6], tx[7]

In [4]:
class Node():
    
    def __init__(self, typ, address):
        self.typ = typ
        self.address = address
        self.txs_in = []
        self.txs_out = []
        
    def add_tx_in(self, tx):
        self.txs_in.append(tx)
        
    def add_tx_out(self, tx):
        self.txs_out.append(tx)
        
    def agg_txs_amounts(self, txs):
        amounts = []
        for tx in txs:
            amounts.append(float(tx[2]))
        return amounts
    
    def txs_time_series(self, txs): #calculate mins between transactions
        times = []
        
        for i, tx in enumerate(txs):
       
            if i == 0:
                continue
                
            d = parser.parse(tx[1])
            d_prev = parser.parse(txs[i - 1][1])
            diff = d - d_prev
            duration_in_s = diff.total_seconds()
            mins = divmod(duration_in_s, 60)[0]
            times.append(mins)
            
        return times
            
    
    def stats(self, l):
        min_val = 0 if len(l) == 0 else min(l)
        max_val = 0 if len(l) == 0 else max(l)
        avg = 0 if len(l) == 0 else mean(l)
        std = 0 if len(l) in [0, 1] else stdev(l)
        
        return len(l), min_val, max_val, avg, std
        
    
    def feature_vector(self):
        in_amounts = self.agg_txs_amounts(self.txs_in)
        out_amounts = self.agg_txs_amounts(self.txs_out)
        all_amounts = self.agg_txs_amounts(self.txs_in + self.txs_out)
        
        in_num, in_min, in_max, in_mean, in_std = self.stats(in_amounts)
        out_num, out_min, out_max, out_mean, out_std = self.stats(out_amounts)
        comb_num, comb_min, comb_max, comb_mean, comb_std = self.stats(all_amounts)

        in_time_series = self.txs_time_series(self.txs_in)
        out_time_series = self.txs_time_series(self.txs_out)
        both = self.txs_in + self.txs_out
        both.sort(key= lambda x: parser.parse(x[1]))
        all_time_series = self.txs_time_series(both)
        
        _, in_ts_min, in_ts_max, in_ts_mean, in_ts_std = self.stats(in_time_series)
        _, out_ts_min, out_ts_max, out_ts_mean, out_ts_std = self.stats(out_time_series)        
        _, all_ts_min, all_ts_max, all_ts_mean, all_ts_std = self.stats(all_time_series)   
        
        
        ls =  [in_num, in_min, in_max, in_mean, in_std,
                out_num, out_min, out_max, out_mean, out_std,
                comb_num, comb_min, comb_max, comb_mean, comb_std,
                in_ts_min, in_ts_max, in_ts_mean, in_ts_std,
                out_ts_min, out_ts_max, out_ts_mean, out_ts_std,
                all_ts_min, all_ts_max, all_ts_mean, all_ts_std
               ]
        
        return np.array(ls)
    
    def one_hot_label(self):
        feature_vec = [0, 0, 0]
        for index, acc in enumerate(['Wallet', 'Smart Contract', 'DEX']):
            if acc == self.typ:
                feature_vec[index] = 1
                break
        return feature_vec
            
        
    
    def __str__(self):
        return f"{self.typ}: {len(self.txs_in)} in, {len(self.txs_out)} out"

In [5]:
nodes = {}

for tx in transactions:
    
    sender, receiver = extract_users(tx)
    sender_typ, receiver_typ = extract_types(tx)
    
    if sender not in nodes:
        nodes[sender] = Node(sender_typ, sender)
    
    if receiver not in nodes:
        nodes[receiver] = Node(receiver_typ, receiver)
        
    nodes[sender].add_tx_out(tx)
    nodes[receiver].add_tx_in(tx)
    
    

In [35]:
for i, (addr, node) in enumerate(nodes.items()):
    if node.typ == 'DEX':
        print(node)
        print(i)
        
    

DEX: 5077 in, 9525 out
62
DEX: 1598 in, 1696 out
971
DEX: 1445 in, 1665 out
3129
DEX: 17 in, 20 out
130439
DEX: 45 in, 45 out
138984
DEX: 5902 in, 5902 out
174551
DEX: 3178 in, 4689 out
174567
DEX: 7 in, 7 out
174954
DEX: 11 in, 11 out
190733
DEX: 8 in, 8 out
195985
DEX: 4701 in, 4701 out
201825
DEX: 3 in, 3 out
219076
DEX: 3 in, 3 out
238808
DEX: 1 in, 91 out
263338
DEX: 1 in, 7 out
283723
DEX: 8305 in, 8305 out
370670
DEX: 3207 in, 3536 out
404353
DEX: 2 in, 2 out
406807
DEX: 1 in, 2 out
406808
DEX: 1 in, 0 out
448348
DEX: 1 in, 0 out
448507
DEX: 3 in, 2 out
490836


In [7]:
addresses = np.empty((0,1), str)
features = np.empty((0,27), dtype='float32')
labels = np.empty((0, 3), int)

In [8]:
for addr, node in nodes.items():
    addresses = np.vstack((addresses, addr))
    features = np.vstack((features, node.feature_vector()))
    labels = np.vstack((labels, node.one_hot_label()))

In [9]:
features

array([[0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [4.46660000e+04, 2.40000000e-17, 2.19997000e+04, ...,
        1.45300000e+03, 3.69951559e+00, 1.46426903e+01],
       [1.00000000e+00, 6.00000000e+00, 6.00000000e+00, ...,
        2.62900000e+03, 2.62900000e+03, 0.00000000e+00],
       ...,
       [1.00000000e+00, 6.19350000e+00, 6.19350000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 5.00959000e+02, 5.00959000e+02, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 8.65520123e+00, 8.65520123e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00]])

In [10]:
mins = features.min(axis=0)
maxs = features.max(axis=0)

In [11]:
normalized_features = (features - mins) / (maxs - mins)

In [12]:
#------------------------------------------------------------------------------------------#
#Above is data preprocessing#
#Below is graph assembly#
#------------------------------------------------------------------------------------------#

In [13]:
node_dict = {}

for i in range(len(addresses)):
    node_dict[addresses[i][0]] = i

In [14]:
u = np.empty((0,1), int)
v = np.empty((0,1), int)
e = np.empty((0,1), float)

In [15]:
for tx in transactions:
    u = np.append(u, node_dict[tx[3]])
    v = np.append(v, node_dict[tx[4]])
    e = np.append(e, float(tx[2]))

In [16]:
#BELOW is GNNS#

In [17]:
import torch
import numpy as np
import networkx as nx
import dgl

Using backend: pytorch


In [18]:
g = dgl.DGLGraph((u,v))

In [19]:
import dgl
import dgl.function as fn
import torch as th
import torch.nn as nn
import torch.nn.functional as F
from dgl import DGLGraph

gcn_msg = fn.copy_src(src='h', out='m')
gcn_reduce = fn.sum(msg='m', out='h')

In [20]:
class GCNLayer(nn.Module):
    
    def __init__(self, in_feats, out_feats):
        super(GCNLayer, self).__init__()
        self.linear = nn.Linear(in_feats, out_feats)
        
        
    def forward(self, g, feature):
        with g.local_scope():
            g.ndata['h'] = feature
            g.update_all(gcn_msg, gcn_reduce)
            h = g.ndata['h']
            return self.linear(h)

In [21]:
# TODO - shuffle g,

In [27]:
from random import randint
length = len(addresses)
train_mask = np.empty((0,1), bool)

mask_border = int(length // 1.25) #80% train, 20% test

for i in range(len(addresses)):
    
        train_mask = np.append(train_mask, True if i < mask_border else False)
        
test_mask = np.invert(train_mask)   


In [23]:
def evaluate(model, g, features, labels, mask):
    model.eval()
    
    with torch.no_grad():
        logits = model(g, features)
        logits = logits[mask]
        labels = labels[mask]
        _, indices = torch.max(logits, dim=1)
        correct = torch.sum(indices == labels)
        
        return correct.item() * 1.0 / len(labels)

In [24]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.layer1 = GCNLayer(27, 16)
        self.layer2 = GCNLayer(16, 3)
        
        
    def forward(self, g, features):
        x = F.relu(self.layer1(g, features))
        x = self.layer2(g, x)
        return x
    
    
net = Net()
net.cuda() #make sure uses GPU
print(net)

Net(
  (layer1): GCNLayer(
    (linear): Linear(in_features=27, out_features=16, bias=True)
  )
  (layer2): GCNLayer(
    (linear): Linear(in_features=16, out_features=3, bias=True)
  )
)


In [28]:
g = g.to(torch.device('cuda:0'))

normalized_features = np.float32(normalized_features)
features_tensor = torch.from_numpy(normalized_features)
features_tensor = features_tensor.to(torch.device('cuda:0'))

labels_tensor = torch.LongTensor(labels)
labels_tensor = labels_tensor.to(torch.device('cuda:0'))
labels_class_indices = torch.max(labels_tensor, 1).indices

train_mask = torch.from_numpy(train_mask)
train_mask = train_mask.to(torch.device('cuda:0'))


test_mask = torch.from_numpy(test_mask)
test_mask = test_mask.to(torch.device('cuda:0'))

In [29]:
import time
import numpy as np
optimizer = torch.optim.Adam(net.parameters(), lr=0.001)
dur = []

for epoch in range(100):
    
    if epoch >= 3:
        t0 = time.time()
        
    net.train()
    logits = net(g, features_tensor)
    logp = F.log_softmax(logits, 1)
    loss = F.nll_loss(logp[train_mask], labels_class_indices[train_mask])
    
    
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()
    
    if epoch >= 3:
        dur.append(time.time() - t0)
        
    acc = evaluate(net, g, features_tensor, labels_class_indices, test_mask)
    print(f"Epoch {epoch} | Loss {loss.item()} | Test acc {acc} | Time(s) {np.mean(dur)}")

/home/hamish/.virtualenvs/transaction-data-ml/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3335: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/hamish/.virtualenvs/transaction-data-ml/lib/python3.6/site-packages/numpy/core/_methods.py:161: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


Epoch 0 | Loss 146.42005920410156 | Test acc 0.9005564692364881 | Time(s) nan
Epoch 1 | Loss 136.89353942871094 | Test acc 0.9004438236420573 | Time(s) nan
Epoch 2 | Loss 127.44799041748047 | Test acc 0.899407484173294 | Time(s) nan
Epoch 3 | Loss 118.23646545410156 | Test acc 0.8970494363965426 | Time(s) 0.022705554962158203
Epoch 4 | Loss 109.26128387451172 | Test acc 0.8879927306043061 | Time(s) 0.02090930938720703
Epoch 5 | Loss 101.04337310791016 | Test acc 0.8829161691486246 | Time(s) 0.020250399907430012
Epoch 6 | Loss 93.17768859863281 | Test acc 0.8445340602729027 | Time(s) 0.019971072673797607
Epoch 7 | Loss 85.32743835449219 | Test acc 0.8172663167143533 | Time(s) 0.019781875610351562
Epoch 8 | Loss 79.34972381591797 | Test acc 0.8156141813293682 | Time(s) 0.01970803737640381
Epoch 9 | Loss 72.72940826416016 | Test acc 0.8190761559315415 | Time(s) 0.01972661699567522
Epoch 10 | Loss 65.20511627197266 | Test acc 0.8434226237411855 | Time(s) 0.020108014345169067
Epoch 11 | Los

Epoch 93 | Loss 2.87052583694458 | Test acc 0.8095763774678773 | Time(s) 0.020371049315064817
Epoch 94 | Loss 6.968619346618652 | Test acc 0.8803103010641253 | Time(s) 0.020384487898453423
Epoch 95 | Loss 3.025239944458008 | Test acc 0.8818197520294981 | Time(s) 0.020396911969748875
Epoch 96 | Loss 3.8805222511291504 | Test acc 0.8819849655679967 | Time(s) 0.020384773294976417
Epoch 97 | Loss 4.427865982055664 | Test acc 0.8820074946868828 | Time(s) 0.0203730256933915
Epoch 98 | Loss 4.6535868644714355 | Test acc 0.8820074946868828 | Time(s) 0.020382662614186604
Epoch 99 | Loss 4.576659679412842 | Test acc 0.8819474170365197 | Time(s) 0.020389866583126106


In [30]:
len(addresses)

665802

In [31]:

test_logits = net(g, features_tensor)
test_logits = test_logits[test_mask]
_, indices = torch.max(test_logits, dim=1)
test_labels = labels_class_indices[test_mask]

In [32]:
test_labels

tensor([0, 0, 1,  ..., 0, 0, 0], device='cuda:0')

In [33]:
confusion_matrix = np.zeros((3,3), int)

for i in range(len(test_labels)):
    accounts = ['Wallet', 'Smart Contract', 'DEX']
    
    pred = indices[i]
    label = test_labels[i]
    
    print(f"Label {accounts[label]}, predicted {accounts[pred]}")
    
    confusion_matrix[label][pred] += 1

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet


Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label Wallet, predicted Smart Contract
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label Wallet, predicted Wallet
Label W

Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label W

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wa

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, p

...

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Smart Contract
Label Wallet, predicted Wallet


Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wa

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, p

Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet


Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Smart Contract, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet
Label Wallet, predicted Wallet


In [34]:
confusion_matrix

array([[116432,   3487,      0],
       [ 12233,   1009,      0],
       [     0,      0,      0]])